In [ ]:
# default_exp scrape13D

# scrape13D

> Scrape holdings information from 13D SEC filings.

In [ ]:
#hide
%load_ext autoreload
%autoreload 2
from nbdev import show_doc

In [ ]:
#export

import collections
import itertools
import numpy as np
import os
from pathlib import Path
import re

from secscan import utils, dailyList, basicInfo, infoScraper, scrape13F, scrape13G

default13DDir = os.path.join(utils.stockDataRoot,'scraped13D')

13D scraper class - scrape holdings information from the SEC filing:

In [ ]:
#export

class scraper13D(infoScraper.scraperBase) :
    def __init__(self, infoDir=default13DDir, startD=None, endD=None, fSuff='m.pkl', **pickle_kwargs) :
        super().__init__(infoDir, 'SC 13D', startD=startD, endD=endD, fSuff=fSuff, **pickle_kwargs)
    def scrapeInfo(self, accNo, formType=None) :
        return scrape13G.parse13GD(accNo, formType=formType), None

Test 13D scraper class:

In [ ]:
dl = dailyList.dailyList(startD='empty')
dl.updateForDays('20210701','20210704')
assert len(dl.getFilingsList(None,'SC 13D')[0])==84,"testing 13D scraper class (daily list count)"
info = scrape13G.parse13GD('0000921895-21-001173', formType='SC 13D/A')
assert (info['ciks']==['0001165002', '0001461945']
        and info['positions']==[('412,925', '5.0'), ('430,214', '5.2'), ('843,139', '10.2'),
                                ('843,139', '10.2'), ('860,416', '10.4'), ('860,416', '10.4')]
        and info['purpose'].startswith('Item 4 is hereby amended and restated to read')
        and info['purpose'].endswith('Item 4 of Schedule 13D. 8 CUSIP No. 961765104')
    ),"testing 13D scraper class (parsing)"

20210703 WEEKEND 20210702 ### list index 63 filings for 20210702: 6569 * 20210701 filings for 20210701: 5573 * 

Combine 13F, 13G, and 13D filings for a quarter:

In [ ]:
#export

def get13GDDatesForQ(y, qNo) :
    _,kwargs = scrape13F.getPeriodAndNextQStartEnd(y, qNo)
    kwargs['startD'] = str(int(kwargs['startD'][:4])-2) + kwargs['startD'][4:]
    return kwargs

def getCombNSSForQ(y, qNo, minFrac=0.01, maxFrac=1.0, minStocksPerInv=3, maxStocksPerInv=100,
                   minTop10Frac=0.4, minAUM=None, dtype=np.float64,
                   minInvestorsPerStock=None, maxInvestorsPerStock=None,
                   minAllInvestorsPerStock=2, maxAllInvestorsPerStock=None, cusipFilter=None,
                   max13GDBonus=0.2, min13GDBonus=0.02, max13GDCount=100,
                   include13F=True, include13G=False, include13D=False,
                   outsInfoFName='', outDir=None) :
    """
    Calculates a matrix of investor holdings for a quarter, based on all 13F filings filed
    during the succeeding quarter, combined with 13G and 13D filings from the previous year
    up through the succeeding quarter.

    Returns mat, ciks, cusips where mat is a matrix of shape (len(ciks), len(cusips))
    in which each row has the fractions held by the corresponding cik in each cusip.

    If minFrac and/or maxFrac is supplied, restricts to stocks with fraction of
    total portfolio >=minFrac and/or <=maxFrac.

    If minStocksPerInv, maxStocksPerInv, minTop10Frac or minAUM are specified, omits
    investors with too few stocks, too many stocks, too small a fraction in the
    top 10 holdings, or too small a total stock value.
    If minInvestorsPerStock is specified, restricts to stocks with at least that many investors
    in the returned matrix; likewise, maxInvestorsPerStock can be used to give an upper bound.
    If minAllInvestorsPerStock or maxAllInvestorsPerStock is specified, restricts based on a count
    of all investors that have any position in each stock.
    If cusipFilter is specified, this should be a function that returns True for cusips to keep.

    13GD bonus fractions are 1.0/#positions, but restricted to [min13GDBonus..max13GDBonus]
    If max13GDCount is not None, restricts to investors with at most max13GDCount combined 13G
    and 13D positions.
    """
    allCusipCounter = collections.Counter()
    cikNames = utils.loadPklFromDir(dailyList.defaultDLDir, 'cikNames.pkl', {})
    cikNames = dict((cik,name) for cik,(name,dStr) in cikNames.items())
    cusipNames = utils.pickLoad(os.path.join(utils.stockDataRoot,'cusipMap.pkl'))
    cik13GDSortedPosMap = None
    if include13G or include13D :
        dates = get13GDDatesForQ(y,qNo)
        scrapedL = []
        if include13G :
            scrapedL.append(scrape13G.scraper13G(**dates))
        if include13D :
            scrapedL.append(scraper13D(**dates))
        cik13GDPosMap = scrape13G.updateCik13GDPos(scrapedL, cusipNames=cusipNames, cikNames=cikNames,
                                                   includeTickers=True)
        cikBonusMaps = [scrape13G.calcBonusMap(cik13GDPosMap,
                                               max13GDBonus=max13GDBonus, min13GDBonus=min13GDBonus,
                                               max13GDCount=max13GDCount, allCusipCounter=allCusipCounter)]
        cik13GDSortedPosMap = dict((cik,sorted(((cusip,pos[-1]) for cusip,pos in posMap.items()),
                                        # sort positions largest first, then by name
                                        key=lambda x : (-x[1], cusipNames.get(x[0],'CUSIP-'+x[0]).lower())))
                                   for cik,posMap in cik13GDPosMap.items())
    else :
        cikBonusMaps = []
    res = scrape13F.getNSSForQ(y, qNo, minFrac=minFrac, maxFrac=maxFrac,
                                minStocksPerInv=minStocksPerInv, maxStocksPerInv=maxStocksPerInv,
                                minTop10Frac=minTop10Frac, minAUM=minAUM, dtype=dtype,
                                minInvestorsPerStock=minInvestorsPerStock,
                                maxInvestorsPerStock=maxInvestorsPerStock,
                                minAllInvestorsPerStock=minAllInvestorsPerStock,
                                maxAllInvestorsPerStock=maxAllInvestorsPerStock,
                                allCusipCounter=allCusipCounter, cusipFilter=cusipFilter,
                                extraHoldingsMaps=cikBonusMaps, include13F=include13F)
    if outsInfoFName is not None :
        if outDir is None :
            outDir = Path(utils.stockDataRoot)
        else :
            outDir = Path(utils.stockDataRoot)/outDir
        if not outDir.exists() :
            outDir.mkdir()
        mat, ciks, cusips = res
        cusipSet = set(cusips)
        mat /= 0.01
        mat = np.minimum(mat,20.0)
        res = {'Y': mat, 'ciks': ciks, 'cusips': cusips, 'cusipinfo': []}
        utils.pickSave(outDir/f'{outsInfoFName}{y}Q{qNo}sInfo.pkl', res,
                       fix_imports=True, protocol=2)
        utils.pickSave(outDir/f'cusipMap.pkl',
                       dict((cusip,cusipNames.get(cusip,'CUSIP-'+cusip))
                            for cusip in allCusipCounter.keys()),
                       fix_imports=True, protocol=2)
        if cik13GDSortedPosMap is not None :
            utils.pickSave(outDir/f'{outsInfoFName}{y}Q{qNo}hold13GD.pkl', cik13GDSortedPosMap,
                           fix_imports=True, protocol=2)
    return res

def oddballScreen(yNo, qNo) :
    """
    Screens for stocks that only one investor reports holding.
    These will mostly be mistakes, so I try to remove the mistakes using cusipFilter.
    """
    cusipNames = utils.pickLoad(os.path.join(utils.stockDataRoot,'cusipMap.pkl'))
    mat, ciks, cusips = getCombNSSForQ(yNo, qNo, max13GDCount=50, include13F=True, include13G=True, include13D=True,
                                       minAllInvestorsPerStock=None, maxAllInvestorsPerStock=1,
                                       cusipFilter = lambda x : x in cusipNames and 'DELETED' not in cusipNames[x])
    return [cusipNames[cusip] for cusip in cusips]

In [ ]:
# for y,qNo in itertools.islice(itertools.product([2018,2019,2020,2021],[1,2,3,4]),14) :
#     m = getCombNSSForQ(y, qNo, outDir='ratingsN')

In [ ]:
# m = getCombNSSForQ(2021, 2, outDir='ratingsNGD',
#                        include13D=True,include13G=True,include13F=False)

No event date in 0000903064-19-000010; using 2019-06-25
No event date in 0000903064-19-000009; using 2019-06-25
No CUSIP in 0001085146-19-001821
No CUSIP in 0000215457-19-008358
No event date in 0000315066-19-001607; using 2019-07-03
No event date in 0000315066-19-001596; using 2019-07-03
No event date in 0000315066-19-001608; using 2019-07-03
No event date in 0000315066-19-001612; using 2019-07-03
No CUSIP in 0000215457-19-008097
No CUSIP in 0000215457-19-008290
No CUSIP in 0000215457-19-008296
No CUSIP in 0000215457-19-008308
No CUSIP in 0000215457-19-008334
No CUSIP in 0000215457-19-008338
No event date in 0000315066-19-001605; using 2019-07-03
No event date in 0000315066-19-001613; using 2019-07-03
No event date in 0000315066-19-001600; using 2019-07-03
No CUSIP in 0001422848-19-000128
No CUSIP in 0001422848-19-000130
No event date in 0000315066-19-001598; using 2019-07-03
No event date in 0000315066-19-001594; using 2019-07-03
No event date in 0000315066-19-001606; using 2019-07-0

No event date in 0001213900-20-004000; using 2020-02-07
No event date in 0000312348-20-000019; using 2020-02-07
missing or ambiguous subject CIK '0000897101-20-000074'
No event date in 0001567619-20-003727; using 2020-02-07
No event date in 0000807985-20-000012; using 2020-02-07
missing or ambiguous subject CIK '0000029332-20-000003'
No event date in 0000312348-20-000014; using 2020-02-07
No event date in 0000312348-20-000015; using 2020-02-07
No event date in 0000312348-20-000018; using 2020-02-07
No event date in 0000807985-20-000006; using 2020-02-07
No event date in 0000807985-20-000008; using 2020-02-07
No event date in 0000807985-20-000004; using 2020-02-07
No event date in 0001140361-20-003341; using 2020-02-07
No event date in 0001140361-20-003347; using 2020-02-07
No event date in 0001140361-20-003352; using 2020-02-07
No CUSIP in 0000926047-20-000002
missing or ambiguous subject CIK '0001474506-20-000056'
missing or ambiguous subject CIK '0000849869-20-000006'
No event date i

No event date in 0000315066-21-001222; using 2021-02-01
No event date in 0000315066-21-001244; using 2021-02-01
No event date in 0000315066-21-001271; using 2021-02-01
No event date in 0000315066-21-001275; using 2021-02-01
No event date in 0000318989-21-000041; using 2021-02-01
No event date in 0000318989-21-000054; using 2021-02-01
No event date in 0000318989-21-000037; using 2021-02-01
No event date in 0000318989-21-000053; using 2021-02-01
missing or ambiguous subject CIK '0001157523-21-000152'
No CUSIP in 0000929638-21-000241
No event date in 0001567619-21-002594; using 2021-02-02
No event date in 0000814133-21-000011; using 2021-02-02
No CUSIP in 0001550913-21-000008
*** No positions found in 0000909012-21-000025
No event date in 0000814133-21-000009; using 2021-02-02
No event date in 0001137774-21-000017; using 2021-02-02
No event date in 0001137774-21-000018; using 2021-02-02
No event date in 0001137774-21-000019; using 2021-02-02
No event date in 0001137774-21-000020; using 20

No CUSIP in 0001193125-20-271258
*** No positions found in 0001193125-20-273461
*** No positions found in 0001193125-20-273458
No event date in 0000904454-20-000667; using 2020-10-16
No CUSIP in 0001193125-20-275604
No CUSIP in 0001193125-20-275600
*** No positions found in 0001104659-20-118751
No CUSIP in 0000950157-20-001291
No CUSIP in 0000929638-20-001072
*** No positions found in 0001193125-20-284909
*** No positions found in 0001193125-20-284910
*** No positions found in 0001193125-20-284914
*** No positions found in 0001193125-20-284918
*** No positions found in 0001193125-20-284911
*** No positions found in 0001193125-20-284912
*** No positions found in 0001193125-20-284915
*** No positions found in 0000928464-20-000069
No CUSIP in 0001140361-20-024605
*** No positions found in 0000895345-20-001079
*** No positions found in 0000899140-20-000523
*** No positions found in 0001104659-20-123165
*** No positions found in 0000928464-20-000072
*** No positions found in 0001193125-20-2

count1 7405 count2 1724
total of 7617 ciks, 57854 13G/D filings
requiring at least 2 ALL investors per stock - removed 1688 stocks
removed a total of 1688 stocks
removed 582 investors with no remaining positions
final counts: 6,472 investors; 5,660 stocks; 16,120 positions


In [ ]:
# for y,qNo in itertools.islice(itertools.product([2018,2019,2020,2021],[1,2,3,4]),14) :
#     m = getCombNSSForQ(y, qNo, outDir='ratingsNGD',
#                        include13D=True,include13G=True,include13F=False)

*** No positions found in 0001213900-17-001484
No event date in 0001193125-17-046129; using 2017-02-09
No CUSIP in 0001615774-17-000692
No CUSIP in 0001615774-17-000686
No CUSIP in 0001615774-17-000688
No CUSIP in 0001615774-17-000690
No event date in 0001140361-17-008016; using 2017-02-10
missing or ambiguous subject CIK '0001286225-17-000005'
*** No positions found in 0001392972-17-000034
*** No positions found in 0001392972-17-000035
missing or ambiguous subject CIK '0000900075-17-000005'
missing or ambiguous subject CIK '0001082327-17-000040'
No event date in 0001387131-17-001042; using 2017-02-16
missing or ambiguous subject CIK '0000897101-17-000249'
*** No positions found in 0001354821-17-000007
No event date in 0001213900-17-001768; using 2017-02-17
No event date in 0001483885-17-000006; using 2017-02-20
No event date in 0001483885-17-000005; using 2017-02-20
No event date in 0001483885-17-000007; using 2017-02-20
No event date in 0001096906-17-000129; using 2017-02-22
No event

missing or ambiguous subject CIK '0001067406-18-000001'
No CUSIP in 0000215457-18-004714
missing or ambiguous subject CIK '0000906318-18-000009'
*** No positions found in 0001193125-18-029310
No event date in 0000903064-18-000002; using 2018-01-25
No CUSIP in 0000215457-18-004556
No event date in 0001137774-18-000035; using 2018-01-25
No event date in 0001137774-18-000036; using 2018-01-25
No event date in 0001137774-18-000037; using 2018-01-25
No event date in 0001137774-18-000038; using 2018-01-25
No event date in 0001137774-18-000039; using 2018-01-25
No event date in 0001137774-18-000041; using 2018-01-25
No CUSIP in 0000215457-18-004525
No CUSIP in 0000215457-18-004536
missing or ambiguous subject CIK '0000943374-18-000037'
No CUSIP in 0000215457-18-004495
No CUSIP in 0000215457-18-004617
No CUSIP in 0000215457-18-004659
No CUSIP in 0000215457-18-004524
No CUSIP in 0000215457-18-004585
No CUSIP in 0000215457-18-004452
No CUSIP in 0000215457-18-004455
No CUSIP in 0000215457-18-0044

No event date in 0001144204-18-008813; using 2018-02-07
No CUSIP in 0001213900-18-001757
missing or ambiguous subject CIK '0001046327-18-000005'
*** No positions found in 0001193125-18-044109
No event date in 0000814133-18-000009; using 2018-02-07
missing or ambiguous subject CIK '0001050463-18-000006'
*** No positions found in 0001193125-18-044082
No event date in 0000312069-18-000013; using 2018-02-07
No CUSIP in 0001073330-18-000006
No CUSIP in 0001073330-18-000008
No event date in 0001193125-18-045411; using 2018-02-07
No CUSIP in 0000894579-18-000085
No CUSIP in 0000894579-18-000087
No CUSIP in 0000894579-18-000089
No event date in 0001099281-18-000005; using 2018-02-07
*** No positions found in 0001193125-18-044277
*** No positions found in 0001193125-18-044289
No CUSIP in 0001615774-18-001209
No event date in 0001019056-18-000365; using 2018-02-07
No CUSIP in 0001422848-18-000276
No CUSIP in 0001422848-18-000355
missing or ambiguous subject CIK '0001117733-18-000012'
*** ERROR i

No CUSIP in 0001021432-17-000334
No CUSIP in 0001504304-17-000069
No CUSIP in 0001144204-17-047431
*** No positions found in 0001144204-17-047865
No CUSIP in 0001493152-17-010527
No CUSIP in 0001021432-17-000343
No event date in 0001193125-17-284623; using 2017-09-07
No CUSIP in 0001493152-17-010664
No CUSIP in 0000009015-17-000014
No event date in 0001493152-17-010679; using 2017-09-08
No CUSIP in 0000009015-17-000016
*** No positions found in 0001104659-17-057659
No CUSIP in 0001615774-17-005201
*** No positions found in 0000928464-17-000043
missing or ambiguous subject CIK '0000944809-17-000011'
No CUSIP in 0001504304-17-000072
*** No positions found in 0001193125-17-293040
*** No positions found in 0001341004-17-000610
No CUSIP in 0001504304-17-000074
No CUSIP in 0001193125-17-302158
No event date in 0001690872-17-000001; using 2017-09-26
No CUSIP in 0001654954-17-009058
*** No positions found in 0001144204-17-051263
*** No positions found in 0001144204-17-051265
No CUSIP in 000150

requiring at least 2 ALL investors per stock - removed 1483 stocks
removed a total of 1483 stocks
removed 560 investors with no remaining positions
final counts: 4,647 investors; 4,130 stocks; 10,896 positions
*** No positions found in 0001213900-17-001484
No event date in 0001193125-17-046129; using 2017-02-09
No CUSIP in 0001615774-17-000692
No CUSIP in 0001615774-17-000686
No CUSIP in 0001615774-17-000688
No CUSIP in 0001615774-17-000690
No event date in 0001140361-17-008016; using 2017-02-10
missing or ambiguous subject CIK '0001286225-17-000005'
*** No positions found in 0001392972-17-000034
*** No positions found in 0001392972-17-000035
missing or ambiguous subject CIK '0000900075-17-000005'
missing or ambiguous subject CIK '0001082327-17-000040'
No event date in 0001387131-17-001042; using 2017-02-16
missing or ambiguous subject CIK '0000897101-17-000249'
*** No positions found in 0001354821-17-000007
No event date in 0001213900-17-001768; using 2017-02-17
No event date in 00014

...

count1 7337 count2 1499
total of 7451 ciks, 57246 13G/D filings
requiring at least 2 ALL investors per stock - removed 1633 stocks
removed a total of 1633 stocks
removed 581 investors with no remaining positions
final counts: 6,299 investors; 5,419 stocks; 15,250 positions
No event date in 0000903064-19-000010; using 2019-06-25
No event date in 0000903064-19-000009; using 2019-06-25
No CUSIP in 0001085146-19-001821
No CUSIP in 0000215457-19-008358
No event date in 0000315066-19-001607; using 2019-07-03
No event date in 0000315066-19-001596; using 2019-07-03
No event date in 0000315066-19-001608; using 2019-07-03
No event date in 0000315066-19-001612; using 2019-07-03
No CUSIP in 0000215457-19-008097
No CUSIP in 0000215457-19-008290
No CUSIP in 0000215457-19-008296
No CUSIP in 0000215457-19-008308
No CUSIP in 0000215457-19-008334
No CUSIP in 0000215457-19-008338
No event date in 0000315066-19-001605; using 2019-07-03
No event date in 0000315066-19-001613; using 2019-07-03
No event date 

No event date in 0001567619-20-003554; using 2020-02-07
No event date in 0001567619-20-003662; using 2020-02-07
No event date in 0001567619-20-003768; using 2020-02-07
No event date in 0001567619-20-003801; using 2020-02-07
No event date in 0001567619-20-003812; using 2020-02-07
No event date in 0001567619-20-003913; using 2020-02-07
No event date in 0001567619-20-003925; using 2020-02-07
No event date in 0001567619-20-003932; using 2020-02-07
No event date in 0001567619-20-003942; using 2020-02-07
No event date in 0001567619-20-003947; using 2020-02-07
No event date in 0001567619-20-004065; using 2020-02-07
No event date in 0001567619-20-004098; using 2020-02-07
No event date in 0001567619-20-003849; using 2020-02-07
*** No positions found in 0001323953-20-000007
*** No positions found in 0001421578-20-000007
No event date in 0000807985-20-000011; using 2020-02-07
No event date in 0001567619-20-003832; using 2020-02-07
*** No positions found in 0001193125-20-036674
*** No positions fo

No event date in 0000318989-21-000040; using 2021-02-01
No event date in 0000315066-21-000877; using 2021-02-01
No event date in 0000315066-21-000821; using 2021-02-01
No event date in 0000315066-21-000881; using 2021-02-01
No event date in 0000315066-21-001311; using 2021-02-01
No event date in 0000315066-21-001196; using 2021-02-01
No event date in 0000315066-21-001022; using 2021-02-01
No event date in 0000315066-21-001240; using 2021-02-01
No event date in 0000318989-21-000042; using 2021-02-01
No event date in 0000318989-21-000036; using 2021-02-01
No event date in 0000315066-21-001018; using 2021-02-01
No event date in 0000315066-21-001301; using 2021-02-01
No event date in 0000315066-21-000842; using 2021-02-01
No event date in 0000318989-21-000046; using 2021-02-01
No event date in 0000315066-21-001235; using 2021-02-01
No event date in 0000315066-21-000927; using 2021-02-01
No event date in 0000315066-21-001262; using 2021-02-01
No event date in 0000315066-21-000928; using 202

No CUSIP in 0001193125-19-276313
No CUSIP in 0001193125-19-276342
No CUSIP in 0001193125-19-276325
*** No positions found in 0001599916-19-000152
No CUSIP in 0001193125-19-279104
No CUSIP in 0001140361-19-019397
No CUSIP in 0001140361-19-019471
No CUSIP in 0001437749-19-021292
No CUSIP in 0001067621-19-000001
No CUSIP in 0001504304-19-000023
missing or ambiguous subject CIK '0000898822-19-000086'
*** No positions found in 0001193125-19-294752
missing or ambiguous subject CIK '0001654954-19-013139'
missing or ambiguous subject CIK '0001654954-19-013142'
No event date in 0001193125-19-295809; using 2019-11-13
No CUSIP in 0001683168-19-003777
No CUSIP in 0001437749-19-023470
No CUSIP in 0001437749-19-023471
*** No positions found in 0001394156-19-000085
No event date in 0001193125-19-299525; using 2019-11-18
*** No positions found in 0001193125-19-299378
*** No positions found in 0000919574-19-007502
No event date in 0000907254-19-000089; using 2019-11-19
missing or ambiguous subject CIK 

requiring at least 2 ALL investors per stock - removed 1687 stocks
removed a total of 1687 stocks
removed 581 investors with no remaining positions
final counts: 6,448 investors; 5,647 stocks; 16,067 positions


In [ ]:
# m = getCombNSSForQ(2021, 1, max13GDCount=50, include13F=True, include13G=True, include13D=True,
#                   minInvestorsPerStock=2, minAllInvestorsPerStock=2)

No event date in 0000814133-20-000050; using 2020-03-31
No event date in 0000814133-20-000049; using 2020-03-31
No event date in 0000814133-20-000051; using 2020-03-31
No CUSIP in 0001193125-20-101055
No event date in 0000071633-20-000016; using 2020-04-01
No event date in 0000071633-20-000017; using 2020-04-01
No event date in 0000071633-20-000018; using 2020-04-01
No event date in 0000071633-20-000019; using 2020-04-01
No event date in 0000071633-20-000020; using 2020-04-01
*** No positions found in 0001104659-20-044338
No event date in 0001140361-20-008343; using 2020-04-01
No event date in 0001140361-20-008347; using 2020-04-01
No CUSIP in 0000834237-20-009334
No CUSIP in 0000834237-20-009337
No CUSIP in 0000834237-20-009361
No CUSIP in 0000834237-20-009336
No CUSIP in 0000834237-20-009354
No CUSIP in 0000834237-20-009381
No CUSIP in 0001422848-20-000110
No CUSIP in 0001422849-20-000133
No event date in 0000866842-20-000004; using 2020-04-02
No event date in 0000318989-20-000068; u

No event date in 0000315066-21-000777; using 2021-02-01
No event date in 0000315066-21-000779; using 2021-02-01
No event date in 0000315066-21-000788; using 2021-02-01
No event date in 0000315066-21-000802; using 2021-02-01
No event date in 0000315066-21-000813; using 2021-02-01
No event date in 0000315066-21-000814; using 2021-02-01
No event date in 0000315066-21-000823; using 2021-02-01
No event date in 0000315066-21-000826; using 2021-02-01
No event date in 0000315066-21-000831; using 2021-02-01
No event date in 0000315066-21-000837; using 2021-02-01
No event date in 0000315066-21-000843; using 2021-02-01
No event date in 0000315066-21-000850; using 2021-02-01
No event date in 0000315066-21-000852; using 2021-02-01
No event date in 0000315066-21-000855; using 2021-02-01
No event date in 0000315066-21-000857; using 2021-02-01
No event date in 0000315066-21-000865; using 2021-02-01
No event date in 0000315066-21-000884; using 2021-02-01
No event date in 0000315066-21-000891; using 202

*** ERROR in  0001062993-20-003675
*** No positions found in 0000928464-20-000032
*** No positions found in 0000928464-20-000038
No CUSIP in 0001140361-20-018334
*** No positions found in 0001193125-20-221658
*** No positions found in 0001213900-20-022576
*** No positions found in 0000928464-20-000047
No CUSIP in 0001193125-20-222595
*** No positions found in 0001193125-20-227106
No event date in 0001469709-20-000075; using 2020-08-14
No CUSIP in 0001104659-20-097611
No CUSIP in 0001104659-20-097995
No CUSIP in 0001193125-20-227517
*** No positions found in 0001599916-20-000104
*** No positions found in 0000928464-20-000032
No CUSIP in 0001437749-20-018845
No CUSIP in 0001104659-20-099576
No event date in 0001193125-20-236405; using 2020-08-24
*** No positions found in 0000928464-20-000053
No CUSIP in 0001493152-20-017170
No CUSIP in 0001493152-20-017178
No CUSIP in 0001104659-20-102831
*** No positions found in 0001193125-20-244724
No CUSIP in 0001104659-20-104723
No CUSIP in 00011046

min stock fraction of portfolio 0.01
max stock fraction of portfolio 1.0
min stocks per investor 3
max stocks per investor 100
min fraction of portfolio in top 10 positions 0.4
period 2021-03-31 - total of 5911 ciks, 6039 13F filings
CIK 1731061 1 - 2 [('20210408', '0001104659-21-047884', 829), ('20210506', '0001104659-21-062185', 895)]
CIK 1386929 1 - 2 [('20210412', '0001386929-21-000005', 79), ('20210414', '0001386929-21-000006', 79)]
CIK 1105410 1 - 2 [('20210413', '0001214659-21-004137', 50), ('20210421', '0001214659-21-004362', 50)]
CIK 1566601 1 - 2 [('20210413', '0001566601-21-000005', 764), ('20210414', '0001566601-21-000006', 764)]
CIK 1573767 1 - 2 [('20210413', '0001573767-21-000006', 49), ('20210505', '0001573767-21-000007', 66)]
CIK 1840740 1 - 2 [('20210413', '0001840740-21-000005', 51), ('20210414', '0001840740-21-000006', 51)]
CIK 1053994 1 - 2 [('20210414', '0001085146-21-001185', 184), ('20210419', '0001085146-21-001232', 296)]
CIK 1381055 2 - 3 [('20210416', '000138

CIK 1063296 1 - 2 [('20210517', '0000905718-21-000694', 10), ('20210518', '0000905718-21-000710', 10)]
CIK 1080383 1 - 2 [('20210517', '0000919574-21-003508', 53), ('20210518', '0000919574-21-003778', 55)]
CIK 1086619 1 - 2 [('20210517', '0001567619-21-010327', 3238), ('20210528', '0001567619-21-011331', 3238)]
CIK 1119376 1 - 2 [('20210517', '0001567619-21-010351', 38), ('20210518', '0001567619-21-010595', 40)]
CIK 1164688 1 - 2 [('20210517', '0001172661-21-001214', 16), ('20210521', '0001172661-21-001373', 16)]
CIK 1224962 1 - 2 [('20210517', '0001012975-21-000229', 138), ('20210610', '0001012975-21-000242', 139)]
CIK 1332784 1 - 2 [('20210517', '0001567619-21-010483', 12), ('20210623', '0001567619-21-012524', 12)]
CIK 1387369 1 - 2 [('20210517', '0000919574-21-003641', 39), ('20210517', '0000919574-21-003738', 40)]
CIK 1393818 1 - 2 [('20210517', '0000950123-21-007113', 500), ('20210519', '0000950123-21-007183', 500)]
CIK 1423053 1 - 3 [('20210517', '0000950123-21-007021', 16138), (

In [ ]:
# m = getCombNSSForQ(2021, 1, max13GDCount=50, include13F=True, include13G=True, include13D=True,
#                   minInvestorsPerStock=None, minAllInvestorsPerStock=2)

No event date in 0000814133-20-000050; using 2020-03-31
No event date in 0000814133-20-000049; using 2020-03-31
No event date in 0000814133-20-000051; using 2020-03-31
No CUSIP in 0001193125-20-101055
No event date in 0000071633-20-000016; using 2020-04-01
No event date in 0000071633-20-000017; using 2020-04-01
No event date in 0000071633-20-000018; using 2020-04-01
No event date in 0000071633-20-000019; using 2020-04-01
No event date in 0000071633-20-000020; using 2020-04-01
*** No positions found in 0001104659-20-044338
No event date in 0001140361-20-008343; using 2020-04-01
No event date in 0001140361-20-008347; using 2020-04-01
No CUSIP in 0000834237-20-009334
No CUSIP in 0000834237-20-009337
No CUSIP in 0000834237-20-009361
No CUSIP in 0000834237-20-009336
No CUSIP in 0000834237-20-009354
No CUSIP in 0000834237-20-009381
No CUSIP in 0001422848-20-000110
No CUSIP in 0001422849-20-000133
No event date in 0000866842-20-000004; using 2020-04-02
No event date in 0000318989-20-000068; u

No event date in 0001493152-21-014761; using 2021-06-14
No event date in 0001213900-21-033106; using 2021-06-14
No event date in 0000315066-21-001589; using 2021-06-16
No CUSIP in 0001829126-21-005509
No CUSIP in 0001104659-21-082805
No event date in 0001564590-20-014752; using 2020-03-25
*** No positions found in 0001072613-20-000155
*** ERROR in  0001567619-20-007639
No CUSIP in 0001437749-20-007781
*** No positions found in 0001193125-20-110664
*** No positions found in 0001079973-20-000328
No event date in 0001493152-20-007486; using 2020-04-24
No CUSIP in 0001104659-20-056666
No event date in 0001493152-20-007889; using 2020-04-30
No CUSIP in 0001104659-20-058005
No event date in 0001104659-20-058917; using 2020-05-01
No event date in 0001493152-20-008005; using 2020-05-01
No CUSIP in 0001683168-20-001488
*** No positions found in 0001104659-20-062674
*** No positions found in 0001104659-20-063178
*** No positions found in 0001104659-20-063182
No CUSIP in 0001493152-20-009325
No C

min stock fraction of portfolio 0.01
max stock fraction of portfolio 1.0
min stocks per investor 3
max stocks per investor 100
min fraction of portfolio in top 10 positions 0.4
period 2021-03-31 - total of 5911 ciks, 6039 13F filings
CIK 1731061 1 - 2 [('20210408', '0001104659-21-047884', 829), ('20210506', '0001104659-21-062185', 895)]
CIK 1386929 1 - 2 [('20210412', '0001386929-21-000005', 79), ('20210414', '0001386929-21-000006', 79)]
CIK 1105410 1 - 2 [('20210413', '0001214659-21-004137', 50), ('20210421', '0001214659-21-004362', 50)]
CIK 1566601 1 - 2 [('20210413', '0001566601-21-000005', 764), ('20210414', '0001566601-21-000006', 764)]
CIK 1573767 1 - 2 [('20210413', '0001573767-21-000006', 49), ('20210505', '0001573767-21-000007', 66)]
CIK 1840740 1 - 2 [('20210413', '0001840740-21-000005', 51), ('20210414', '0001840740-21-000006', 51)]
CIK 1053994 1 - 2 [('20210414', '0001085146-21-001185', 184), ('20210419', '0001085146-21-001232', 296)]
CIK 1381055 2 - 3 [('20210416', '000138

CIK 1119376 1 - 2 [('20210517', '0001567619-21-010351', 38), ('20210518', '0001567619-21-010595', 40)]
CIK 1164688 1 - 2 [('20210517', '0001172661-21-001214', 16), ('20210521', '0001172661-21-001373', 16)]
CIK 1224962 1 - 2 [('20210517', '0001012975-21-000229', 138), ('20210610', '0001012975-21-000242', 139)]
CIK 1332784 1 - 2 [('20210517', '0001567619-21-010483', 12), ('20210623', '0001567619-21-012524', 12)]
CIK 1387369 1 - 2 [('20210517', '0000919574-21-003641', 39), ('20210517', '0000919574-21-003738', 40)]
CIK 1393818 1 - 2 [('20210517', '0000950123-21-007113', 500), ('20210519', '0000950123-21-007183', 500)]
CIK 1423053 1 - 3 [('20210517', '0000950123-21-007021', 16138), ('20210521', '0000950123-21-007261', 16138), ('20210521', '0000950123-21-007263', 3)]
CIK 1595082 0 - 2 [('20210517', '0001595082-21-000039', 453), ('20210527', '0001595082-21-000041', 1)]
CIK 1604350 1 - 2 [('20210517', '0001567619-21-010535', 24), ('20210521', '0001567619-21-010963', 24)]
CIK 1621855 2 - 3 [('2

In [ ]:
# ll = oddballScreen(2021,2)

No event date in 0000903064-19-000010; using 2019-06-25
No event date in 0000903064-19-000009; using 2019-06-25
No CUSIP in 0001085146-19-001821
No CUSIP in 0000215457-19-008358
No event date in 0000315066-19-001607; using 2019-07-03
No event date in 0000315066-19-001596; using 2019-07-03
No event date in 0000315066-19-001608; using 2019-07-03
No event date in 0000315066-19-001612; using 2019-07-03
No CUSIP in 0000215457-19-008097
No CUSIP in 0000215457-19-008290
No CUSIP in 0000215457-19-008296
No CUSIP in 0000215457-19-008308
No CUSIP in 0000215457-19-008334
No CUSIP in 0000215457-19-008338
No event date in 0000315066-19-001605; using 2019-07-03
No event date in 0000315066-19-001613; using 2019-07-03
No event date in 0000315066-19-001600; using 2019-07-03
No CUSIP in 0001422848-19-000128
No CUSIP in 0001422848-19-000130
No event date in 0000315066-19-001598; using 2019-07-03
No event date in 0000315066-19-001594; using 2019-07-03
No event date in 0000315066-19-001606; using 2019-07-0

No event date in 0001567619-20-000034; using 2019-12-26
No event date in 0001437749-20-000012; using 2019-12-26
No event date in 0001437749-20-000015; using 2019-12-26
No event date in 0000790502-20-000007; using 2019-12-30
No event date in 0000790502-20-000003; using 2019-12-30
No event date in 0000790502-20-000004; using 2019-12-30
No event date in 0000790502-20-000006; using 2019-12-30
No event date in 0000790502-20-000005; using 2019-12-30
No event date in 0000790502-20-000001; using 2019-12-30
No event date in 0000790502-20-000002; using 2019-12-30
No event date in 0001567619-20-000711; using 2019-12-31
No event date in 0001085146-20-000030; using 2020-01-01
No event date in 0000071633-20-000003; using 2020-01-01
No event date in 0000071633-20-000004; using 2020-01-01
No event date in 0000071633-20-000001; using 2020-01-01
No event date in 0000071633-20-000002; using 2020-01-01
*** No positions found in 0001104659-20-002126
No event date in 0001717174-20-000002; using 2020-01-01
N

No CUSIP in 0000834237-21-001272
No CUSIP in 0000834237-21-001205
No CUSIP in 0000834237-21-001213
No CUSIP in 0000834237-21-001215
No CUSIP in 0000834237-21-001388
No CUSIP in 0001512022-21-000001
No CUSIP in 0001535384-21-000004
No CUSIP in 0001535384-21-000002
*** ERROR in  0001104659-21-007373
No CUSIP in 0000834237-21-002183
No CUSIP in 0000834237-21-002168
No CUSIP in 0001085146-21-000262
No CUSIP in 0000834237-21-002104
No CUSIP in 0000834237-21-002170
No CUSIP in 0000834237-21-002172
No CUSIP in 0000834237-21-002176
No CUSIP in 0000834237-21-002177
No CUSIP in 0000834237-21-002187
No CUSIP in 0000834237-21-002202
No CUSIP in 0000834237-21-002209
No CUSIP in 0000834237-21-002214
No CUSIP in 0000834237-21-002228
No CUSIP in 0001213900-21-004611
*** No positions found in 0001292814-21-000217
No event date in 0001085146-21-000299; using 2021-01-21
No event date in 0001085146-21-000300; using 2021-01-21
No CUSIP in 0000834237-21-004594
No CUSIP in 0000834237-21-004614
No CUSIP in 00

*** No positions found in 0001193125-20-284910
*** No positions found in 0001193125-20-284914
*** No positions found in 0001193125-20-284918
*** No positions found in 0001193125-20-284911
*** No positions found in 0001193125-20-284912
*** No positions found in 0001193125-20-284915
*** No positions found in 0000928464-20-000069
No CUSIP in 0001140361-20-024605
*** No positions found in 0000895345-20-001079
*** No positions found in 0000899140-20-000523
*** No positions found in 0001104659-20-123165
*** No positions found in 0000928464-20-000072
*** No positions found in 0001193125-20-295156
*** No positions found in 0001193125-20-295157
*** No positions found in 0001193125-20-295154
*** No positions found in 0001193125-20-295170
*** No positions found in 0001193125-20-295160
*** No positions found in 0001193125-20-295166
*** No positions found in 0001193125-20-295580
*** No positions found in 0001193125-20-295582
No CUSIP in 0001171520-20-000457
No event date in 0000899681-20-000044; us

min stock fraction of portfolio 0.01
max stock fraction of portfolio 1.0
min stocks per investor 3
max stocks per investor 100
min fraction of portfolio in top 10 positions 0.4
period 2021-06-30 - total of 5945 ciks, 6099 13F filings
CIK 1755670 1 - 2 [('20210708', '0001755670-21-000004', 396), ('20210804', '0001755670-21-000005', 509)]
CIK 1842560 1 - 2 [('20210709', '0001842560-21-000003', 332), ('20210709', '0001842560-21-000004', 332)]
CIK 1353395 1 - 2 [('20210712', '0001085146-21-001901', 260), ('20210713', '0001085146-21-001945', 154)]
CIK 1092903 1 - 2 [('20210713', '0001096906-21-001592', 708), ('20210805', '0001096906-21-001852', 708)]
CIK 1026720 1 - 2 [('20210715', '0001012975-21-000271', 24), ('20210831', '0001012975-21-000336', 24)]
CIK 1840740 1 - 2 [('20210720', '0001840740-21-000007', 52), ('20210720', '0001840740-21-000008', 52)]
CIK 1609674 1 - 2 [('20210721', '0001609674-21-000004', 175), ('20210816', '0001609674-21-000005', 176)]
CIK 1666786 1 - 2 [('20210721', '00

CIK 1769302 1 - 2 [('20210813', '0001420506-21-001077', 1138), ('20210813', '0001420506-21-001146', 1138)]
CIK 1773206 0 - 2 [('20210813', '0001420506-21-001147', 142), ('20210830', '0001420506-21-001346', 71)]
CIK 1820879 0 - 2 [('20210813', '0001820879-21-000003', 1975), ('20210819', '0001085146-21-002618', 498)]
CIK 1844873 2 - 3 [('20210813', '0001844873-21-000004', 81), ('20210816', '0001844873-21-000006', 81), ('20210817', '0001844873-21-000007', 81)]
CIK 1869028 1 - 2 [('20210813', '0001398344-21-016180', 2), ('20210823', '0001398344-21-016691', 2)]
CIK 898427 1 - 2 [('20210813', '0000898427-21-000016', 2347), ('20210813', '0000898427-21-000017', 2351)]
CIK 932859 1 - 2 [('20210813', '0000950123-21-010884', 4190), ('20210903', '0000950123-21-012109', 3592)]
CIK 1011443 0 - 2 [('20210816', '0001011443-21-000012', 796), ('20210910', '0001011443-21-000015', 4)]
CIK 1084580 1 - 2 [('20210816', '0001085146-21-002551', 1648), ('20210820', '0001085146-21-002619', 1626)]
CIK 1144208 1 -

ValueError: too many values to unpack (expected 3)

In [ ]:
# m = getCombNSSForQ(2021, 1, max13GDCount=50)

No event date in 0000814133-20-000050; using 2020-03-31
No event date in 0000814133-20-000049; using 2020-03-31
No event date in 0000814133-20-000051; using 2020-03-31
No CUSIP in 0001193125-20-101055
No event date in 0000071633-20-000016; using 2020-04-01
No event date in 0000071633-20-000017; using 2020-04-01
No event date in 0000071633-20-000018; using 2020-04-01
No event date in 0000071633-20-000019; using 2020-04-01
No event date in 0000071633-20-000020; using 2020-04-01
*** No positions found in 0001104659-20-044338
No event date in 0001140361-20-008343; using 2020-04-01
No event date in 0001140361-20-008347; using 2020-04-01
No CUSIP in 0000834237-20-009334
No CUSIP in 0000834237-20-009337
No CUSIP in 0000834237-20-009361
No CUSIP in 0000834237-20-009336
No CUSIP in 0000834237-20-009354
No CUSIP in 0000834237-20-009381
No CUSIP in 0001422848-20-000110
No CUSIP in 0001422849-20-000133
No event date in 0000866842-20-000004; using 2020-04-02
No event date in 0000318989-20-000068; u

*** No positions found in 0001072613-20-000155
*** ERROR in  0001567619-20-007639
No CUSIP in 0001437749-20-007781
*** No positions found in 0001193125-20-110664
*** No positions found in 0001079973-20-000328
No event date in 0001493152-20-007486; using 2020-04-24
No CUSIP in 0001104659-20-056666
No event date in 0001493152-20-007889; using 2020-04-30
No CUSIP in 0001104659-20-058005
No event date in 0001104659-20-058917; using 2020-05-01
No event date in 0001493152-20-008005; using 2020-05-01
No CUSIP in 0001683168-20-001488
*** No positions found in 0001104659-20-062674
*** No positions found in 0001104659-20-063178
*** No positions found in 0001104659-20-063182
No CUSIP in 0001493152-20-009325
No CUSIP in 0001504304-20-000037
No CUSIP in 0001140361-20-011974
No event date in 0001718111-20-000002; using 2020-05-15
No event date in 0001718111-20-000003; using 2020-05-15
No CUSIP in 0000919574-20-003809
No CUSIP in 0001504304-20-000038
*** No positions found in 0000928464-20-000023
No 

min stock fraction of portfolio 0.01
max stock fraction of portfolio 1.0
min stocks per investor 3
max stocks per investor 100
min fraction of portfolio in top 10 positions 0.4
period 2021-03-31 - total of 5911 ciks, 6039 13F filings
CIK 1731061 1 - 2 [('20210408', '0001104659-21-047884', 829), ('20210506', '0001104659-21-062185', 895)]
CIK 1386929 1 - 2 [('20210412', '0001386929-21-000005', 79), ('20210414', '0001386929-21-000006', 79)]
CIK 1105410 1 - 2 [('20210413', '0001214659-21-004137', 50), ('20210421', '0001214659-21-004362', 50)]
CIK 1566601 1 - 2 [('20210413', '0001566601-21-000005', 764), ('20210414', '0001566601-21-000006', 764)]
CIK 1573767 1 - 2 [('20210413', '0001573767-21-000006', 49), ('20210505', '0001573767-21-000007', 66)]
CIK 1840740 1 - 2 [('20210413', '0001840740-21-000005', 51), ('20210414', '0001840740-21-000006', 51)]
CIK 1053994 1 - 2 [('20210414', '0001085146-21-001185', 184), ('20210419', '0001085146-21-001232', 296)]
CIK 1381055 2 - 3 [('20210416', '000138

CIK 1063296 1 - 2 [('20210517', '0000905718-21-000694', 10), ('20210518', '0000905718-21-000710', 10)]
CIK 1080383 1 - 2 [('20210517', '0000919574-21-003508', 53), ('20210518', '0000919574-21-003778', 55)]
CIK 1086619 1 - 2 [('20210517', '0001567619-21-010327', 3238), ('20210528', '0001567619-21-011331', 3238)]
CIK 1119376 1 - 2 [('20210517', '0001567619-21-010351', 38), ('20210518', '0001567619-21-010595', 40)]
CIK 1164688 1 - 2 [('20210517', '0001172661-21-001214', 16), ('20210521', '0001172661-21-001373', 16)]
CIK 1224962 1 - 2 [('20210517', '0001012975-21-000229', 138), ('20210610', '0001012975-21-000242', 139)]
CIK 1332784 1 - 2 [('20210517', '0001567619-21-010483', 12), ('20210623', '0001567619-21-012524', 12)]
CIK 1387369 1 - 2 [('20210517', '0000919574-21-003641', 39), ('20210517', '0000919574-21-003738', 40)]
CIK 1393818 1 - 2 [('20210517', '0000950123-21-007113', 500), ('20210519', '0000950123-21-007183', 500)]
CIK 1423053 1 - 3 [('20210517', '0000950123-21-007021', 16138), (

In [ ]:
# m = scrape13F.getNSSForQ(2021,1)

min stock fraction of portfolio 0.01
max stock fraction of portfolio 1.0
min stocks per investor 3
max stocks per investor 100
min fraction of portfolio in top 10 positions 0.4
period 2021-03-31 - total of 5911 ciks, 6039 13F filings
CIK 1731061 1 - 2 [('20210408', '0001104659-21-047884', 829), ('20210506', '0001104659-21-062185', 895)]
CIK 1386929 1 - 2 [('20210412', '0001386929-21-000005', 79), ('20210414', '0001386929-21-000006', 79)]
CIK 1105410 1 - 2 [('20210413', '0001214659-21-004137', 50), ('20210421', '0001214659-21-004362', 50)]
CIK 1566601 1 - 2 [('20210413', '0001566601-21-000005', 764), ('20210414', '0001566601-21-000006', 764)]
CIK 1573767 1 - 2 [('20210413', '0001573767-21-000006', 49), ('20210505', '0001573767-21-000007', 66)]
CIK 1840740 1 - 2 [('20210413', '0001840740-21-000005', 51), ('20210414', '0001840740-21-000006', 51)]
CIK 1053994 1 - 2 [('20210414', '0001085146-21-001185', 184), ('20210419', '0001085146-21-001232', 296)]
CIK 1381055 2 - 3 [('20210416', '000138

CIK 1119376 1 - 2 [('20210517', '0001567619-21-010351', 38), ('20210518', '0001567619-21-010595', 40)]
CIK 1164688 1 - 2 [('20210517', '0001172661-21-001214', 16), ('20210521', '0001172661-21-001373', 16)]
CIK 1224962 1 - 2 [('20210517', '0001012975-21-000229', 138), ('20210610', '0001012975-21-000242', 139)]
CIK 1332784 1 - 2 [('20210517', '0001567619-21-010483', 12), ('20210623', '0001567619-21-012524', 12)]
CIK 1387369 1 - 2 [('20210517', '0000919574-21-003641', 39), ('20210517', '0000919574-21-003738', 40)]
CIK 1393818 1 - 2 [('20210517', '0000950123-21-007113', 500), ('20210519', '0000950123-21-007183', 500)]
CIK 1423053 1 - 3 [('20210517', '0000950123-21-007021', 16138), ('20210521', '0000950123-21-007261', 16138), ('20210521', '0000950123-21-007263', 3)]
CIK 1595082 0 - 2 [('20210517', '0001595082-21-000039', 453), ('20210527', '0001595082-21-000041', 1)]
CIK 1604350 1 - 2 [('20210517', '0001567619-21-010535', 24), ('20210521', '0001567619-21-010963', 24)]
CIK 1621855 2 - 3 [('2

In [ ]:
#hide
# assorted test code: 

# dl = dailyList.dailyList(startD='20200101')

# s = scraper13D(startD='empty')
# s.updateForDays(dl,startD='20210702',endD='20210703')
# print(); s.printCounts()

# dailyList.dlCountFilings(startD='20210726',endD='20210731',formClass='13F-HR',noAmend=False)

# accNo = '0001174947-20-001195'
# i = parse13D(accNo,'SC 13D')
# i

# for accNo,info in s.infoMap['20210702'].items() :
#     print(accNo,info['positions'])

# b = utils.downloadSecUrl('',toFormat='souptext')
# utils.secBrowse('0001104659-21-079401')
# scrape13G.parse13GD('0001171520-19-000289')

In [ ]:
#hide
# uncomment and run to regenerate all library Python files
# from nbdev.export import notebook2script; notebook2script()